In [15]:
import matplotlib.pyplot as plt
from datetime import datetime, timedelta
import plotly.graph_objects as go
import datetime
import pandas as pd
import csv
import os
import time
from dateutil import tz
import glob
import quandl as q
import re
import plotly.graph_objects as go
import numpy as np
import streamlit as st
from plotly.subplots import make_subplots

st.set_page_config(layout="wide")
# %%
from fredapi import Fred

In [16]:
api_key_fred = os.environ['api_key_fred']
fred = Fred(api_key=api_key_fred)
quandl_api_key = os.environ['quandl_api_key']

In [17]:
# # # start - read in BTC data # # #
datasource_btcusd = "BITFINEX/BTCUSD.csv"
# dogeusd_data = pd.read_csv("coindata/{}".format(
#     datasource_btcusd.replace("/", " ")), index_col=0)
# dogeusd_data.index = pd.to_datetime(dogeusd_data.index)

# most_recent_stored_btcusd_date = dogeusd_data.sort_index().tail(1).index[0].strftime("%Y-%m-%d")
todays_date = datetime.date.today() - timedelta(days=1)
todays_date = todays_date.strftime("%Y-%m-%d")
datasource_btcusd.split(".")[0]

'BITFINEX/BTCUSD'

In [18]:

data = q.get("BITFINEX/BTCUSD", start_date='2017-01-01',
                 end_date='{}'.format(todays_date),
                 api_key=quandl_api_key)
data.info()
data["First"] = data.Last.shift(1)
data = data.dropna()
data

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 2442 entries, 2017-01-01 to 2023-10-07
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   High    2442 non-null   float64
 1   Low     2442 non-null   float64
 2   Mid     2436 non-null   float64
 3   Last    2442 non-null   float64
 4   Bid     2436 non-null   float64
 5   Ask     2436 non-null   float64
 6   Volume  2442 non-null   float64
dtypes: float64(7)
memory usage: 152.6 KB


High       Low       Mid      Last       Bid       Ask  \
Date                                                                    
2017-01-02   1006.5    961.26    998.29    999.24    997.34    999.24   
2017-01-03   1035.0    994.10   1019.45   1019.50   1019.30   1019.60   
2017-01-04   1040.0   1013.50   1038.50   1038.00   1038.00   1039.00   
2017-01-05   1150.0   1036.40   1138.65   1139.60   1138.60   1138.70   
2017-01-06   1166.0    850.79   1003.75   1003.40   1003.60   1003.90   
...             ...       ...       ...       ...       ...       ...   
2023-10-03  27700.0  27176.00  27315.50  27313.00  27315.00  27316.00   
2023-10-04  27846.0  27211.00  27795.50  27785.00  27795.00  27796.00   
2023-10-05  28134.0  27369.00  27471.50  27472.00  27471.00  27472.00   
2023-10-06  28297.0  27195.00  28052.50  28050.00  28052.00  28053.00   
2023-10-07  28026.0  27840.00  27959.50  27962.00  27959.00  27960.00   

                  Volume     First  
Date                                
2017-01-02  13440.456264    966.61  
2017-01-03  21804.197216    999.24  
2017-01-04  14128.625714   1019.50  
2017-01-05  53698.692041   1038.00  
2017-01-06  91218.600678   1139.60  
...                  ...       ...  
2023-10-03    844.470243  27556.00  
2023-10-04    878.152923  27313.00  
2023-10-05   1442.610646  27785.00  
2023-10-06   1624.134094  27472.00  
2023-10-07    452.295827  28050.00  

[2435 rows x 8 columns]

In [19]:
dogeusd_data = data.sort_index()
# store current df with up-to-date values
dogeusd_data.to_csv('coindata/{}'.format(
    datasource_btcusd.replace("/", " ")), index=True)

In [20]:
# # # start - data processing # # #
dogeusd_data = dogeusd_data.dropna()
dogeusd_data["350_movingaverage"] = pd.Series.rolling(
    dogeusd_data["Last"], window=350, min_periods=1).mean()
dogeusd_data["111_movingaverage"] = pd.Series.rolling(
    dogeusd_data["Last"], window=111, min_periods=1).mean()
# # # end - data processing # # #


In [21]:
# run_it = st.sidebar.button('Show visualizations')

# TODO: Future integrate ETH
# display_name_all_twitter_user_scraped_csvs, all_twitter_user_scraped_csvs = get_all_stored_crypto_csvs()
# display_name_user_selection_list_containing_twitter_user = st.sidebar.selectbox(
#     "Select existing Twitter-User", list(display_name_all_twitter_user_scraped_csvs), 0)


In [22]:
# # # start - get data from fred api and store csv # # #
# # GET S&P DATA
# Billions of Dollars 
data_SP500 = fred.get_series('SP500')
data_SP500 = data_SP500.sort_index()
# store current df with up-to-date values
data_SP500.to_csv('coindata/data_SP500.csv', index=True)

# # Assets: Total Assets: Total Assets: Wednesday Level (RESPPANWW)
#Assets: Total Assets: Total Assets: Wednesday Level (RESPPANWW) Millions of Dollars
data_WALCL = fred.get_series('WALCL')
data_WALCL.dropna()
data_WALCL = data_WALCL.sort_index()
# store current df with up-to-date values
data_WALCL.to_csv('coindata/data_WALCL.csv', index=True)

# # Overnight Reverse Repurchase Agreements Treasury Securities Sold by the Federal Reserve in the Temporary Open Market Operations (RRPONTSYD)
data_RRPONTSYD = fred.get_series('RRPONTSYD')
#Assets: Total Assets: Total Assets: Wednesday Level (RESPPANWW)
# Billions of U.S. Dollars
# data_FRED_RRPONTSYD.values = data_FRED_RRPONTSYD.values * 1000 
data_RRPONTSYD = data_RRPONTSYD * 1000 
data_RRPONTSYD.dropna()
data_RRPONTSYD = data_RRPONTSYD.sort_index()
# store current df with up-to-date values
data_RRPONTSYD.to_csv('coindata/data_RRPONTSYD.csv', index=True)

# # Deposits with Federal Reserve Banks, other than Reserve Balances: U.S. Treasury, General Account (WTREGEN)
# Billions of Dollars 
data_FRED_WTREGEN = fred.get_series('WTREGEN')
data_FRED_WTREGEN = data_FRED_WTREGEN * 1000

data_FRED_WTREGEN.dropna()
data_FRED_WTREGEN = data_FRED_WTREGEN.sort_index()
# store current df with up-to-date values
data_FRED_WTREGEN.to_csv('coindata/data_FRED_WTREGEN.csv', index=True)

# # net liquidity vs s&p500 weekly - Diagram
datasource_fred_total_assets = "data_WALCL.csv"
fred_total_assets = pd.read_csv("coindata/{}".format(
    datasource_fred_total_assets.replace("/", " ")), index_col=0)
fred_total_assets.index = pd.to_datetime(fred_total_assets.index)

most_recent_stored_fred_rrpontsyd_date = fred_total_assets.sort_index().tail(
    1).index[0].strftime("%Y-%m-%d")
todays_date = datetime.date.today() - timedelta(days=1)
todays_date = todays_date.strftime("%Y-%m-%d")

datasource_FRED_WTREGEN = "data_FRED_WTREGEN.csv"
FRED_WTREGEN_data = pd.read_csv("coindata/{}".format(
    datasource_FRED_WTREGEN.replace("/", " ")), index_col=0)
FRED_WTREGEN_data.index = pd.to_datetime(FRED_WTREGEN_data.index)

most_recent_stored_FRED_WTREGEN_date = FRED_WTREGEN_data.sort_index().tail(
    1).index[0].strftime("%Y-%m-%d")

datasource_FRED_RRPONTSYD = "data_RRPONTSYD.csv"
FRED_RRPONTSYD_data = pd.read_csv("coindata/{}".format(
    datasource_FRED_RRPONTSYD.replace("/", " ")), index_col=0)
FRED_RRPONTSYD_data.index = pd.to_datetime(FRED_RRPONTSYD_data.index)

most_recent_stored_FRED_RRPONTSYD_date = FRED_RRPONTSYD_data.sort_index().tail(
    1).index[0].strftime("%Y-%m-%d")

# # # end - get data from fred api and store csv # # #

In [23]:
dogeusd_data = dogeusd_data[(dogeusd_data.index > '2020-08-11 00:00:00')]

In [24]:
import warnings
warnings.filterwarnings("ignore")
from astral import moon
import datetime

# take the data_SP500 index and iterate over it to get the moon phase for each day
# the make a new df out of it called df_moon_phase
df_moon_phase = pd.DataFrame()
for i in data_SP500.index:
    df_moon_phase = df_moon_phase.append({"date": i, "moon_phase": moon.phase(i)}, ignore_index=True)

df_moon_phase["moon_phase"] = df_moon_phase["moon_phase"].astype(int)
df_moon_phase["date"] = pd.to_datetime(df_moon_phase["date"])
df_moon_phase["date"] = df_moon_phase["date"].dt.date
df_moon_phase = df_moon_phase.set_index("date")

# check the relationship between moon phase and dogeusd_data
# merge sp500 with moon phase
dogeusd_data_and_moon_phase = pd.merge(
    dogeusd_data, df_moon_phase, left_index=True, right_index=True, how='left')
dogeusd_data_and_moon_phase = dogeusd_data_and_moon_phase.dropna()
dogeusd_data_and_moon_phase["350_movingaverage"] = pd.Series.rolling(
    dogeusd_data_and_moon_phase["Last"], window=350, min_periods=1).mean()
dogeusd_data_and_moon_phase["111_movingaverage"] = pd.Series.rolling(
    dogeusd_data_and_moon_phase["Last"], window=111, min_periods=1).mean()

# calculat the daily price change for dogeusd_data_and_moon_phase in percentage
dogeusd_data_and_moon_phase["daily_price_change"] = dogeusd_data_and_moon_phase["Last"].pct_change()
dogeusd_data_and_moon_phase["daily_price_change"] = dogeusd_data_and_moon_phase["daily_price_change"].fillna(0)
# calculat the daily price change for dogeusd_data_and_moon_phase in absolut values
dogeusd_data_and_moon_phase["daily_price_change_abs"] = dogeusd_data_and_moon_phase["Last"].diff()
dogeusd_data_and_moon_phase["daily_price_change_abs"] = dogeusd_data_and_moon_phase["daily_price_change_abs"].fillna(0)
dogeusd_data_and_moon_phase

High           Low      Mid          Last      Bid      Ask  \
Date                                                                         
2020-08-13  11822.0  11279.000000  11775.5  11775.020474  11775.0  11776.0   
2020-08-14  11869.0  11650.038909  11768.5  11768.341760  11768.0  11769.0   
2020-08-17  12490.0  11675.000000  12391.5  12389.000000  12391.0  12392.0   
2020-08-18  12407.0  11814.000000  12058.5  12058.963936  12058.0  12059.0   
2020-08-19  12068.0  11608.596047  11787.5  11787.913047  11787.0  11788.0   
...             ...           ...      ...           ...      ...      ...   
2023-10-02  28611.0  27335.000000  27549.5  27556.000000  27549.0  27550.0   
2023-10-03  27700.0  27176.000000  27315.5  27313.000000  27315.0  27316.0   
2023-10-04  27846.0  27211.000000  27795.5  27785.000000  27795.0  27796.0   
2023-10-05  28134.0  27369.000000  27471.5  27472.000000  27471.0  27472.0   
2023-10-06  28297.0  27195.000000  28052.5  28050.000000  28052.0  28053.0   

                 Volume         First  350_movingaverage  111_movingaverage  \
Date                                                                          
2020-08-13  5633.033043  11326.000000       11775.020474       11775.020474   
2020-08-14  4728.208375  11775.020474       11771.681117       11771.681117   
2020-08-17  9775.120654  11905.000000       11977.454078       11977.454078   
2020-08-18  7203.652573  12389.000000       11997.831542       11997.831542   
2020-08-19  6524.191460  12058.963936       11955.847843       11955.847843   
...                 ...           ...                ...                ...   
2023-10-02  2235.010483  27940.000000       23740.061254       27933.405405   
2023-10-03   844.470243  27556.000000       23727.149825       27926.801802   
2023-10-04   878.152923  27313.000000       23721.484111       27917.774775   
2023-10-05  1442.610646  27785.000000       23712.661254       27902.990991   
2023-10-06  1624.134094  27472.000000       23707.706968       27896.288288   

            moon_phase  daily_price_change  daily_price_change_abs  
Date                                                                
2020-08-13        22.0            0.000000                0.000000  
2020-08-14        23.0           -0.000567               -6.678714  
2020-08-17        26.0            0.052740              620.658240  
2020-08-18        27.0           -0.026639             -330.036064  
2020-08-19         0.0           -0.022477             -271.050889  
...                ...                 ...                     ...  
2023-10-02        17.0            0.024501              659.000000  
2023-10-03        18.0           -0.008818             -243.000000  
2023-10-04        19.0            0.017281              472.000000  
2023-10-05        20.0           -0.011265             -313.000000  
2023-10-06        21.0            0.021040              578.000000  

[822 rows x 13 columns]

In [25]:
# now we want the relationship of the moon_phase column on the daily_price_change and daily_price_change_abs column
# we group by the moon_phase column and calculate the mean of the daily_price_change and daily_price_change_abs column
dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase.groupby("moon_phase").mean()
dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase_grouped.reset_index()
dogeusd_data_and_moon_phase_grouped


moon_phase          High           Low           Mid          Last  \
0          0.0  34428.611705  32262.984865  33420.906250  33420.801914   
1          1.0  32748.208343  30794.780308  31659.410714  31658.771884   
2          2.0  35104.619320  33220.649215  34233.150000  34235.252282   
3          3.0  34781.973941  33057.527416  34113.913793  34111.715314   
4          4.0  33545.741815  31786.951556  32558.821429  32559.320804   
5          5.0  32436.141187  30670.655172  31536.379310  31536.574276   
6          6.0  33490.500000  31384.538904  32672.265625  32671.991958   
7          7.0  34376.790874  32270.552238  33353.629032  33352.994480   
8          8.0  31688.716040  29968.533333  30658.666667  30658.839600   
9          9.0  33595.928571  31555.856137  32419.696429  32419.808722   
10        10.0  33876.921317  31680.044814  32766.925926  32766.676404   
11        11.0  31704.781780  29835.886166  30883.116667  30884.764808   
12        12.0  31430.040823  29796.181679  30653.177419  30654.490286   
13        13.0  33185.556082  31253.960832  32381.034483  32380.514269   
14        14.0  32450.954926  30423.233333  31277.383333  31276.991993   
15        15.0  32045.874801  30411.474634  31285.267857  31285.242394   
16        16.0  33818.468386  31928.974770  32852.517857  32852.428721   
17        17.0  32165.922732  30279.397501  31226.017857  31225.059666   
18        18.0  32594.296210  31027.897565  31949.327586  31949.813517   
19        19.0  33206.795403  31396.559625  32368.258065  32369.951692   
20        20.0  32013.266582  30192.828646  31115.233333  31116.535994   
21        21.0  31529.585865  29888.890772  30685.833333  30685.617989   
22        22.0  33265.292536  31694.776188  32709.303030  32707.227704   
23        23.0  32806.252049  31002.614267  31985.758621  31986.233947   
24        24.0  34778.362970  32849.182559  34114.634615  34114.499180   
25        25.0  33013.866667  31286.438121  32247.233333  32248.562327   
26        26.0  32919.132051  30939.034483  32144.206897  32199.655172   
27        27.0  34056.577822  32163.751797  33285.166667  33284.508441   

             Bid           Ask       Volume         First  350_movingaverage  \
0   33420.093750  33421.718750  6696.655972  33528.058104       31754.242382   
1   31658.142857  31660.678571  6464.834245  31970.775923       30772.387806   
2   34232.200000  34234.100000  6469.141140  34207.510636       30878.311016   
3   34112.862069  34114.965517  5439.188124  33816.718568       31643.504691   
4   32557.714286  32559.928571  6332.943953  32862.052762       32904.375310   
5   31535.413793  31537.344828  5151.696826  31530.459580       28824.193251   
6   32670.968750  32673.562500  6939.994612  32639.451531       30002.061048   
7   33352.741935  33354.516129  6573.663945  33669.394982       32548.144743   
8   30657.366667  30659.966667  5714.517489  30951.015787       30711.372761   
9   32419.071429  32420.321429  7483.593492  32791.281449       29971.826793   
10  32764.925926  32768.925926  9296.804263  33121.915679       31690.175301   
11  30881.533333  30884.700000  6477.122839  30698.724492       30931.543270   
12  30651.677419  30654.677419  5890.951370  30569.847537       30214.425696   
13  32380.137931  32381.931034  6551.466923  32140.934183       30923.086948   
14  31276.333333  31278.433333  8150.187615  31616.939712       30784.662390   
15  31284.428571  31286.107143  6748.006236  31352.352882       30706.419976   
16  32851.178571  32853.857143  5871.864171  32849.331783       31025.870474   
17  31224.607143  31227.428571  6507.931911  31323.260255       31920.944843   
18  31948.344828  31950.310345  4602.202508  31541.012614       30214.947580   
19  32366.645161  32369.870968  6222.004978  32378.483405       30941.483636   
20  31114.100000  31116.366667  5492.300937  31108.650287       30936.751337   
21  30684.766667  30686.900000  5436.070738  30696.078678       31529.537594   
22  32708.333333 

In [26]:
# # plot the moon_phase vs the daily_price_change as seperate lines with the time on the x-axis
# fig_moon_phase = make_subplots(specs=[[{"secondary_y": True}]])
# fig_moon_phase.add_trace(
#     go.Scatter(
#         x=dogeusd_data_and_moon_phase_grouped["moon_phase"],
#         y=dogeusd_data_and_moon_phase_grouped["daily_price_change"],
#         name="daily_price_change",
#         mode='lines',
#         marker=dict(color="red"),
#     )
# )

# fig_moon_phase

In [27]:
dogeusd_data_and_moon_phase["validate_ta_logic_category"] = ""
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] > 11) | (dogeusd_data_and_moon_phase["moon_phase"] <= 3), "validate_ta_logic_category"] = "long"
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >3) & (dogeusd_data_and_moon_phase["moon_phase"] <=11), "validate_ta_logic_category"] = "short"
dogeusd_data_and_moon_phase

High           Low      Mid          Last      Bid      Ask  \
Date                                                                         
2020-08-13  11822.0  11279.000000  11775.5  11775.020474  11775.0  11776.0   
2020-08-14  11869.0  11650.038909  11768.5  11768.341760  11768.0  11769.0   
2020-08-17  12490.0  11675.000000  12391.5  12389.000000  12391.0  12392.0   
2020-08-18  12407.0  11814.000000  12058.5  12058.963936  12058.0  12059.0   
2020-08-19  12068.0  11608.596047  11787.5  11787.913047  11787.0  11788.0   
...             ...           ...      ...           ...      ...      ...   
2023-10-02  28611.0  27335.000000  27549.5  27556.000000  27549.0  27550.0   
2023-10-03  27700.0  27176.000000  27315.5  27313.000000  27315.0  27316.0   
2023-10-04  27846.0  27211.000000  27795.5  27785.000000  27795.0  27796.0   
2023-10-05  28134.0  27369.000000  27471.5  27472.000000  27471.0  27472.0   
2023-10-06  28297.0  27195.000000  28052.5  28050.000000  28052.0  28053.0   

                 Volume         First  350_movingaverage  111_movingaverage  \
Date                                                                          
2020-08-13  5633.033043  11326.000000       11775.020474       11775.020474   
2020-08-14  4728.208375  11775.020474       11771.681117       11771.681117   
2020-08-17  9775.120654  11905.000000       11977.454078       11977.454078   
2020-08-18  7203.652573  12389.000000       11997.831542       11997.831542   
2020-08-19  6524.191460  12058.963936       11955.847843       11955.847843   
...                 ...           ...                ...                ...   
2023-10-02  2235.010483  27940.000000       23740.061254       27933.405405   
2023-10-03   844.470243  27556.000000       23727.149825       27926.801802   
2023-10-04   878.152923  27313.000000       23721.484111       27917.774775   
2023-10-05  1442.610646  27785.000000       23712.661254       27902.990991   
2023-10-06  1624.134094  27472.000000       23707.706968       27896.288288   

            moon_phase  daily_price_change  daily_price_change_abs  \
Date                                                                 
2020-08-13        22.0            0.000000                0.000000   
2020-08-14        23.0           -0.000567               -6.678714   
2020-08-17        26.0            0.052740              620.658240   
2020-08-18        27.0           -0.026639             -330.036064   
2020-08-19         0.0           -0.022477             -271.050889   
...                ...                 ...                     ...   
2023-10-02        17.0            0.024501              659.000000   
2023-10-03        18.0           -0.008818             -243.000000   
2023-10-04        19.0            0.017281              472.000000   
2023-10-05        20.0           -0.011265             -313.000000   
2023-10-06        21.0            0.021040              578.000000   

           validate_ta_logic_category  
Date                                   
2020-08-13                       long  
2020-08-14                       long  
2020-08-17                       long  
2020-08-18                       long  
2020-08-19                       long  
...                               ...  
2023-10-02                       long  
2023-10-03                       long  
2023-10-04                       long  
2023-10-05                       long  
2023-10-06                       long  

[822 rows x 14 columns]

In [28]:
# 0 .. 6.99	New moon
# 7 .. 13.99	First quarter
# 14 .. 20.99	Full moon
# 21 .. 27.99	Last quarter
# create a new column called moon_phase_category and fill it with the moon_phase_category
dogeusd_data_and_moon_phase["moon_phase_category"] = ""
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 0) & (dogeusd_data_and_moon_phase["moon_phase"] <= 6.99), "moon_phase_category"] = "New moon"
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 7) & (dogeusd_data_and_moon_phase["moon_phase"] <= 13.99), "moon_phase_category"] = "First quarter"
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 14) & (dogeusd_data_and_moon_phase["moon_phase"] <= 20.99), "moon_phase_category"] = "Full moon"
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 21) & (dogeusd_data_and_moon_phase["moon_phase"] <= 27.99), "moon_phase_category"] = "Last quarter"
dogeusd_data_and_moon_phase

High           Low      Mid          Last      Bid      Ask  \
Date                                                                         
2020-08-13  11822.0  11279.000000  11775.5  11775.020474  11775.0  11776.0   
2020-08-14  11869.0  11650.038909  11768.5  11768.341760  11768.0  11769.0   
2020-08-17  12490.0  11675.000000  12391.5  12389.000000  12391.0  12392.0   
2020-08-18  12407.0  11814.000000  12058.5  12058.963936  12058.0  12059.0   
2020-08-19  12068.0  11608.596047  11787.5  11787.913047  11787.0  11788.0   
...             ...           ...      ...           ...      ...      ...   
2023-10-02  28611.0  27335.000000  27549.5  27556.000000  27549.0  27550.0   
2023-10-03  27700.0  27176.000000  27315.5  27313.000000  27315.0  27316.0   
2023-10-04  27846.0  27211.000000  27795.5  27785.000000  27795.0  27796.0   
2023-10-05  28134.0  27369.000000  27471.5  27472.000000  27471.0  27472.0   
2023-10-06  28297.0  27195.000000  28052.5  28050.000000  28052.0  28053.0   

                 Volume         First  350_movingaverage  111_movingaverage  \
Date                                                                          
2020-08-13  5633.033043  11326.000000       11775.020474       11775.020474   
2020-08-14  4728.208375  11775.020474       11771.681117       11771.681117   
2020-08-17  9775.120654  11905.000000       11977.454078       11977.454078   
2020-08-18  7203.652573  12389.000000       11997.831542       11997.831542   
2020-08-19  6524.191460  12058.963936       11955.847843       11955.847843   
...                 ...           ...                ...                ...   
2023-10-02  2235.010483  27940.000000       23740.061254       27933.405405   
2023-10-03   844.470243  27556.000000       23727.149825       27926.801802   
2023-10-04   878.152923  27313.000000       23721.484111       27917.774775   
2023-10-05  1442.610646  27785.000000       23712.661254       27902.990991   
2023-10-06  1624.134094  27472.000000       23707.706968       27896.288288   

            moon_phase  daily_price_change  daily_price_change_abs  \
Date                                                                 
2020-08-13        22.0            0.000000                0.000000   
2020-08-14        23.0           -0.000567               -6.678714   
2020-08-17        26.0            0.052740              620.658240   
2020-08-18        27.0           -0.026639             -330.036064   
2020-08-19         0.0           -0.022477             -271.050889   
...                ...                 ...                     ...   
2023-10-02        17.0            0.024501              659.000000   
2023-10-03        18.0           -0.008818             -243.000000   
2023-10-04        19.0            0.017281              472.000000   
2023-10-05        20.0           -0.011265             -313.000000   
2023-10-06        21.0            0.021040              578.000000   

           validate_ta_logic_category moon_phase_category  
Date                                                       
2020-08-13                       long        Last quarter  
2020-08-14                       long        Last quarter  
2020-08-17                       long        Last quarter  
2020-08-18                       long        Last quarter  
2020-08-19                       long            New moon  
...                               ...                 ...  
2023-10-02                       long           Full moon  
2023-10-03                       long           Full moon  
2023-10-04                       long           Full moon  
2023-10-05                       long           Full moon  
2023-10-06                       long        Last quarter  

[822 rows x 15 columns]

In [29]:
# group the dogeusd_data_and_moon_phase by the moon_phase_category column and calculate the mean of the daily_price_change and daily_price_change_abs column
dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase.groupby("moon_phase_category").mean()
dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase_grouped.reset_index()
dogeusd_data_and_moon_phase_grouped

moon_phase_category          High           Low           Mid          Last  \
0       First quarter  32813.401549  30890.734866  31854.237864  31854.514470   
1           Full moon  32614.800679  30808.529169  31725.056373  31725.369588   
2        Last quarter  33156.173564  31372.526175  32415.921569  32423.595171   
3            New moon  33808.202391  31893.009732  32903.581731  32903.528681   

            Bid           Ask       Volume         First  350_movingaverage  \
0  31852.985437  31855.490291  6809.219215  31968.171950       31002.633832   
1  31723.857843  31726.254902  6231.368375  31739.649554       30928.198395   
2  32414.867647  32416.975490  5809.197264  32234.201175       30953.948796   
3  32902.519231  32904.644231  6230.387048  32951.793254       30957.036768   

   111_movingaverage  moon_phase  daily_price_change  daily_price_change_abs  
0       31187.058079    9.990291           -0.002034             -133.605504  
1       30913.734227   17.034314            0.002465               45.550551  
2       31241.069350   23.921569            0.006730              223.346855  
3       31282.987370    3.000000            0.000288              -53.160372

In [30]:
# # group the dogeusd_data_and_moon_phase by the moon_phase_category column and calculate the mean of the daily_price_change and daily_price_change_abs column
# dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase.groupby("validate_ta_logic_category").mean()
# dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase_grouped.reset_index()
# dogeusd_data_and_moon_phase_grouped
# validate_ta_logic_category	High	Low	Mid	Last	Bid	Ask	Volume	First	350_movingaverage	111_movingaverage	moon_phase	daily_price_change	daily_price_change_abs
# 0	long	0.154273	0.138621	0.146826	0.146832	0.146752	0.146901	1.979144e+07	0.146288	0.214739	0.173295	15.864286	0.001697	0.000425
# 1	short	0.149864	0.132988	0.140668	0.140678	0.140597	0.140739	2.557094e+07	0.143205	0.212704	0.170402	7.509091	-0.004078	-0.002268

In [31]:
# Correlation Analysis: First, it would be good to calculate the correlation coefficient between the moon_phase_category and the daily_price_change
# we use the pandas function corr() to calculate the correlation coefficient
dogeusd_data_and_moon_phase["daily_price_change"].corr(dogeusd_data_and_moon_phase["moon_phase"])

0.08110504172563995

In [32]:
# Regression Analysis: A linear regression model could be used to predict the BTC price change based on the moon phase. If the model is statistically significant (which you can check using a hypothesis test for the model parameters), this would suggest that there is a relationship. Moreover, the regression coefficients can be interpreted as the expected change in the BTC price for each phase of the moon.
# we use the statsmodels package to run the regression
import statsmodels.api as sm
# we need to add a constant term to the data set to estimate the intercept of the linear regression model
X = sm.add_constant(dogeusd_data_and_moon_phase["moon_phase"])
# we run the regression
model = sm.OLS(dogeusd_data_and_moon_phase["daily_price_change"], X)
results = model.fit()
# we print the summary of the regression
print(results.summary())


                            OLS Regression Results                            
Dep. Variable:     daily_price_change   R-squared:                       0.007
Model:                            OLS   Adj. R-squared:                  0.005
Method:                 Least Squares   F-statistic:                     5.430
Date:                Sun, 08 Oct 2023   Prob (F-statistic):             0.0200
Time:                        17:30:24   Log-Likelihood:                 1488.6
No. Observations:                 822   AIC:                            -2973.
Df Residuals:                     820   BIC:                            -2964.
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         -0.0035      0.003     -1.309      0.1

In [33]:
#                          OLS Regression Results                              
# ==================================================================================
# Dep. Variable:     daily_price_change_abs   R-squared:                       0.007
# Model:                                OLS   Adj. R-squared:                  0.006
# Method:                     Least Squares   F-statistic:                     5.527
# Date:                    Thu, 20 Jul 2023   Prob (F-statistic):             0.0190
# Time:                            16:08:07   Log-Likelihood:                -6671.4
# No. Observations:                     765   AIC:                         1.335e+04
# Df Residuals:                         763   BIC:                         1.336e+04
# Df Model:                               1                                         
# Covariance Type:                nonrobust                                         
# ==============================================================================
#                  coef    std err          t      P>|t|      [0.025      0.975]
# ------------------------------------------------------------------------------
# const       -186.6173    104.328     -1.789      0.074    -391.421      18.186
# moon_phase    15.6265      6.647      2.351      0.019       2.578      28.675
# ==============================================================================
# Omnibus:                       77.255   Durbin-Watson:                   1.994
# Prob(Omnibus):                  0.000   Jarque-Bera (JB):              478.758
# Skew:                          -0.151   Prob(JB):                    1.09e-104
# Kurtosis:                       6.864   Cond. No.                         30.6
# ==============================================================================

# Notes:
# [1] Standard Errors assume that the covariance matrix of the errors is correctly specified.

# Your regression output indicates that the moon phase variable is significant at the 5% level (since the p-value, denoted as "P>|t|" for "moon_phase",
# is less than 0.05). This means there is evidence to suggest that the moon phase has some influence on the absolute daily price change of Bitcoin.

# However, be careful in interpreting the magnitude and meaning of this relationship. The coefficient for "moon_phase" is 15.6265, 
# which means that for each unit increase in moon phase, the model predicts an average increase of 15.6265 units in the absolute daily price change of Bitcoin. 
# But because moon phase is probably a categorical variable coded as numbers, it might not make much sense to think about "unit increases" in this way.

# Moreover, the R-squared value of the model is quite low (0.007), meaning that the moon phase only explains a very small portion of the variation 
# in the absolute daily price change of Bitcoin. This suggests that there are many other factors influencing Bitcoin's daily price change, 
# and that the moon phase alone is not a strong predictor.

# Also, it's important to note that this is a simple linear regression analysis, and it doesn't account for potential confounding variables or 
# other complexities of financial time-series data, such as autocorrelation or non-stationarity.

# It's also worth mentioning again that correlation does not imply causation. Just because there is a statistically significant 
# relationship between moon phase and Bitcoin's price change, it doesn't mean the moon phase is causing these price changes.
# It could be due to chance or other variables that happen to correlate with the moon phase.

In [34]:
dogeusd_data_and_moon_phase.head()

High           Low      Mid          Last      Bid      Ask  \
Date                                                                         
2020-08-13  11822.0  11279.000000  11775.5  11775.020474  11775.0  11776.0   
2020-08-14  11869.0  11650.038909  11768.5  11768.341760  11768.0  11769.0   
2020-08-17  12490.0  11675.000000  12391.5  12389.000000  12391.0  12392.0   
2020-08-18  12407.0  11814.000000  12058.5  12058.963936  12058.0  12059.0   
2020-08-19  12068.0  11608.596047  11787.5  11787.913047  11787.0  11788.0   

                 Volume         First  350_movingaverage  111_movingaverage  \
Date                                                                          
2020-08-13  5633.033043  11326.000000       11775.020474       11775.020474   
2020-08-14  4728.208375  11775.020474       11771.681117       11771.681117   
2020-08-17  9775.120654  11905.000000       11977.454078       11977.454078   
2020-08-18  7203.652573  12389.000000       11997.831542       11997.831542   
2020-08-19  6524.191460  12058.963936       11955.847843       11955.847843   

            moon_phase  daily_price_change  daily_price_change_abs  \
Date                                                                 
2020-08-13        22.0            0.000000                0.000000   
2020-08-14        23.0           -0.000567               -6.678714   
2020-08-17        26.0            0.052740              620.658240   
2020-08-18        27.0           -0.026639             -330.036064   
2020-08-19         0.0           -0.022477             -271.050889   

           validate_ta_logic_category moon_phase_category  
Date                                                       
2020-08-13                       long        Last quarter  
2020-08-14                       long        Last quarter  
2020-08-17                       long        Last quarter  
2020-08-18                       long        Last quarter  
2020-08-19                       long            New moon

In [35]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Normalizing the 'Volume'
dogeusd_data_and_moon_phase['norm_volume'] = (dogeusd_data_and_moon_phase['Volume'] - dogeusd_data_and_moon_phase['Volume'].min()) / (dogeusd_data_and_moon_phase['Volume'].max() - dogeusd_data_and_moon_phase['Volume'].min())

# Calculate daily price change
dogeusd_data_and_moon_phase['daily_change'] = dogeusd_data_and_moon_phase['Last'].diff()

# Assign colors based on positive or negative change
dogeusd_data_and_moon_phase['color'] = np.where(dogeusd_data_and_moon_phase['daily_change'] > 0, 'green', 'red')

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(
        x=dogeusd_data_and_moon_phase.index,
        y=dogeusd_data_and_moon_phase['Last'],
        mode='markers+lines',
        marker=dict(
            size=dogeusd_data_and_moon_phase['norm_volume']*10,  # Scale marker size
            color=dogeusd_data_and_moon_phase['color']  # Assign color based on 'daily_change'
        ),
        name='Last',
        line=dict(color='black')
    ),
    secondary_y=False
)

fig.add_trace(
    go.Bar(
        x=dogeusd_data_and_moon_phase.index,
        y=dogeusd_data_and_moon_phase['Volume'],
        name='Volume',
        marker=dict(color='black')
    ),
    secondary_y=True
)

# Add figure title and labels
fig.update_layout(
    title_text="DOGEUSD Last and Volume",
    xaxis_title="Date",
    yaxis_title="Last",
    yaxis2_title="Volume",
    xaxis_rangeslider_visible=True,
)

# Show the plot
fig.show()


In [36]:
import datetime
import requests

In [37]:
def get_binance_btcusd():
    URL = "https://api.binance.com/api/v3/klines"
    start_str = '2014-01-01 00:00:00'
    fmt = '%Y-%m-%d %H:%M:%S'
    start_time = int(time.mktime(time.strptime(start_str, fmt)) * 1000)
    last_open_time = 0  # added this line

    df = pd.DataFrame()

    while True:
        parameters = {
            'symbol': 'BTCUSDT',
            'interval': '1d',
            'startTime': start_time,
            'limit': 1000  # maximum limit
        }

        response = requests.get(URL, params=parameters)
        data = json.loads(response.text)
        
        if len(data) == 0 or last_open_time == start_time:  # updated this line
            break

        temp_df = pd.DataFrame(data, columns=['Open_time', 'Open', 'High', 'Low', 'Close', 'Volume', 
                                              'Close_time', 'Quote_asset_volume', 'Number_of_trades', 
                                              'Taker_buy_base', 'Taker_buy_quote', 'Ignore'])
        temp_df['Open_time'] = pd.to_datetime(temp_df['Open_time'], unit='ms')
        temp_df['Date'] = temp_df['Open_time'].dt.date
        temp_df['High'] = temp_df['High'].astype(float)
        temp_df['Low'] = temp_df['Low'].astype(float)
        temp_df['Last'] = temp_df['Close'].astype(float)
        temp_df['Volume'] = temp_df['Volume'].astype(float)
        temp_df['Mid'] = (temp_df['High'] + temp_df['Low']) / 2
        temp_df['First'] = temp_df['Last'].shift()

        df = pd.concat([df, temp_df])
        last_open_time = start_time  # added this line
        start_time = int(temp_df['Open_time'].dt.to_pydatetime()[-1].timestamp() * 1000) + 1

    df = df[['Date', 'High', 'Low', 'Mid', 'Last', 'Volume', 'First']]
    df.to_csv('coindata/binance_btcusdt.csv', index=False)

datasource_btcusd = "binance_btcusdt.csv"
btcusd_data = pd.read_csv("coindata/{}".format(datasource_btcusd), index_col=0)
btcusd_data.index = pd.to_datetime(btcusd_data.index)

most_recent_stored_btcusd_date = (
    btcusd_data.sort_index().tail(1).index[0].strftime("%Y-%m-%d")
)

todays_date = datetime.date.today()
todays_date = todays_date.strftime("%Y-%m-%d")


# if most_recent_stored_btcusd_date != todays_date:
# get_binance_btcusd()

# create moon diagrams

In [38]:
# 0 .. 6.99	New moon
# 7 .. 13.99	First quarter
# 14 .. 20.99	Full moon
# 21 .. 27.99	Last quarter
# create a new column called moon_phase_category and fill it with the moon_phase_category
dogeusd_data_and_moon_phase["moon_phase_category"] = ""
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 0) & (dogeusd_data_and_moon_phase["moon_phase"] <= 6.99), "moon_phase_category"] = 0
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 7) & (dogeusd_data_and_moon_phase["moon_phase"] <= 13.99), "moon_phase_category"] = 7
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 14) & (dogeusd_data_and_moon_phase["moon_phase"] <= 20.99), "moon_phase_category"] = 14
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 21) & (dogeusd_data_and_moon_phase["moon_phase"] <= 27.99), "moon_phase_category"] = 21


In [39]:
# make a new plot and plot the daily_price_change of btc by time on the x-axis
fig_btc_price_change = make_subplots(specs=[[{"secondary_y": True}]])
fig_btc_price_change.add_trace(
    go.Scatter(
        x=dogeusd_data_and_moon_phase.index,
        y=dogeusd_data_and_moon_phase["Last"],
        name="Last",
        mode='lines',
        marker=dict(color="red"),
    )
)

# # now add the moon_phase column as a second y-axis
# fig_btc_price_change.add_trace(
#     go.Scatter(
#         x=dogeusd_data_and_moon_phase.index,
#         y=dogeusd_data_and_moon_phase["moon_phase_category"],
#         name="moon_phase",
#         mode='lines',
#         marker=dict(color="blue"),
#     ),
#     secondary_y=True,
# )

last_moon_phase = None

for i in range(len(dogeusd_data_and_moon_phase)):
    current_moon_phase = dogeusd_data_and_moon_phase['moon_phase_category'].iloc[i]
    if current_moon_phase != last_moon_phase:  # check if the moon phase category changed
        if current_moon_phase == 0:  
            fig_btc_price_change.add_annotation(
                x=dogeusd_data_and_moon_phase.index[i],
                y=0.9,
                text="🌑",
                showarrow=False,
                font=dict(
                    size=16,
                ),
                xref="x",
                yref="paper",  # Position annotation relative to the entire plot
                yanchor="bottom",  # Anchor the bottom of the text at y
            )
        elif current_moon_phase == 14: 
            fig_btc_price_change.add_annotation(
                x=dogeusd_data_and_moon_phase.index[i],
                y=0,
                text="🌕",
                showarrow=False,
                font=dict(
                    size=16,
                ),
                xref="x",
                yref="paper",  # Position annotation relative to the entire plot
                yanchor="bottom",  # Anchor the bottom of the text at y
            )
        last_moon_phase = current_moon_phase  # update the last moon phase

fig_btc_price_change

In [40]:
asd

NameError: name 'asd' is not defined

In [ ]:
dogeusd_data_and_moon_phase.tail(6)

High       Low       Mid      Last       Bid       Ask  \
Date                                                                     
2023-07-28  0.077977  0.076128  0.077591  0.077560  0.077570  0.077612   
2023-07-31  0.079879  0.076834  0.077784  0.077798  0.077769  0.077798   
2023-08-01  0.078382  0.075459  0.077238  0.077276  0.077199  0.077276   
2023-08-02  0.078364  0.073856  0.074621  0.074654  0.074604  0.074638   
2023-08-03  0.075092  0.072662  0.073835  0.073821  0.073813  0.073857   
2023-08-04  0.074950  0.072560  0.073457  0.073437  0.073456  0.073459   

                  Volume     First  350_movingaverage  111_movingaverage  \
Date                                                                       
2023-07-28  4.153710e+06  0.077365           0.081208           0.074039   
2023-07-31  4.114400e+06  0.077814           0.081011           0.074009   
2023-08-01  4.528323e+06  0.077798           0.080822           0.073972   
2023-08-02  3.529204e+06  0.077276           0.080625           0.073918   
2023-08-03  3.420566e+06  0.074654           0.080439           0.073845   
2023-08-04  3.006331e+06  0.073821           0.080245           0.073781   

            moon_phase  daily_price_change  daily_price_change_abs  \
Date                                                                 
2023-07-28         9.0            0.002521                0.000195   
2023-07-31        12.0            0.003069                0.000238   
2023-08-01        13.0           -0.006710               -0.000522   
2023-08-02        14.0           -0.033930               -0.002622   
2023-08-03        15.0           -0.011158               -0.000833   
2023-08-04        16.0           -0.005202               -0.000384   

           validate_ta_logic_category moon_phase_category  norm_volume  \
Date                                                                     
2023-07-28                      short                   7     0.008555   
2023-07-31                       long                   7     0.008457   
2023-08-01                       long                   7     0.009487   
2023-08-02                       long                  14     0.007001   
2023-08-03                       long                  14     0.006731   
2023-08-04                       long                  14     0.005700   

            daily_change  color  
Date                             
2023-07-28      0.000195  green  
2023-07-31      0.000238  green  
2023-08-01     -0.000522    red  
2023-08-02     -0.002622    red  
2023-08-03     -0.000833    red  
2023-08-04     -0.000384    red

In [ ]:
# Resistance Support levels automated finding

In [ ]:
btcusd_data

High       Low        Mid      Last        Volume     First
Date                                                                       
2017-08-17   4485.39   4200.74   4343.065   4285.08    795.150377       NaN
2017-08-18   4371.52   3938.77   4155.145   4108.37   1199.888264   4285.08
2017-08-19   4184.69   3850.00   4017.345   4139.98    381.309763   4108.37
2017-08-20   4211.08   4032.62   4121.850   4086.29    467.083022   4139.98
2017-08-21   4119.62   3911.79   4015.705   4016.00    691.743060   4086.29
...              ...       ...        ...       ...           ...       ...
2023-07-20  30417.46  29570.96  29994.210  29800.00  37540.681930  29909.21
2023-07-21  30061.70  29726.34  29894.020  29901.72  23881.408650  29800.00
2023-07-22  29999.00  29625.10  29812.050  29794.00  14660.404670  29901.72
2023-07-23  30350.00  29730.00  30040.000  30116.01  15881.638540  29794.00
2023-07-23  30350.00  29730.00  30040.000  30116.01  15881.638540       NaN

[2170 rows x 6 columns]

In [ ]:
import pandas as pd

window_length = 14  # Define a window length

# Identify resistance levels
btcusd_data['Resistance'] = btcusd_data['High'].rolling(window=window_length).max()
btcusd_data['Resistance']

Date
2017-08-17        NaN
2017-08-18        NaN
2017-08-19        NaN
2017-08-20        NaN
2017-08-21        NaN
               ...   
2023-07-20    31804.2
2023-07-21    31804.2
2023-07-22    31804.2
2023-07-23    31804.2
2023-07-23    31804.2
Name: Resistance, Length: 2170, dtype: float64

In [ ]:
import pandas as pd
import numpy as np
import yfinance as yf
import plotly.graph_objects as go

num_zones = 8

data = btcusd_data

# Calculate zone range
vol_by_price = pd.cut(data['Last'], bins=num_zones).value_counts().sort_index()

# Define zones based on volume
zones = vol_by_price.index.values

# Define support and resistance levels
support_levels = [zone.left for zone in zones]
resistance_levels = [zone.right for zone in zones]

# Plot price and volume-by-price (support and resistance levels)
fig = go.Figure(data=[go.Candlestick(x=data.index,
                open=data['First'],
                high=data['High'],
                low=data['Low'],
                close=data['Last'])])

# Add support and resistance lines
for level in support_levels:
    fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", name=f'Support {level}'))

for level in resistance_levels:
    fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", name=f'Resistance {level}'))

fig.update_layout(title="only price-occurances", xaxis_rangeslider_visible=False)
fig.show()


In [ ]:
support_levels

[3124.683,
 11231.121,
 19273.222,
 27315.324,
 35357.425,
 43399.526,
 51441.628,
 59483.729]

In [ ]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# assuming btcusd_data is your DataFrame and it's indexed by date
data = btcusd_data

# Defining number of bars for volume profile
num_bars = 10

# Calculate frequencies of prices
vol_profile = data['Mid'].value_counts().nlargest(num_bars)

# Define support and resistance levels
support_levels = vol_profile.index.sort_values()
resistance_levels = support_levels[1:]

# Normalize volumes to range 1-5 for line widths
vol_normalized = (vol_profile - vol_profile.min()) / (vol_profile.max() - vol_profile.min()) * 4 + 1

# Plot price and volume profile (support and resistance levels)
fig = go.Figure(data=[go.Candlestick(x=data.index,
                open=data['Mid'],
                high=data['High'],
                low=data['Low'],
                close=data['Last'])])

# # Add support and resistance lines
# for level in support_levels:
#     width = vol_normalized[level]
#     fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", 
#                              line=dict(width=width), name=f'Support {level} Vol: {vol_profile[level]}'))

for level in resistance_levels:
    width = vol_normalized[level]
    fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", 
                             line=dict(width=width), name=f'Resistance {level} Vol: {vol_profile[level]}'))

fig.update_layout(title='BTC-USD', xaxis_rangeslider_visible=False)
fig.show()


In [ ]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# assuming btcusd_data is your DataFrame and it's indexed by date
data = btcusd_data

# Defining number of bars for volume profile
num_bars = 30

# Calculate frequencies of prices
vol_profile = data['Last'].value_counts().nlargest(num_bars)
# Define support and resistance levels
support_levels = vol_profile.index.sort_values()
resistance_levels = support_levels[1:]

# Normalize volumes to range 1-5 for line widths
vol_normalized = (vol_profile - vol_profile.min()) / (vol_profile.max() - vol_profile.min()) * 4 + 1

# Plot price and volume profile (support and resistance levels)
fig = go.Figure(data=[go.Candlestick(x=data.index,
                open=data['First'],
                high=data['High'],
                low=data['Low'],
                close=data['Last'])])

# Add support and resistance lines
for level in resistance_levels:
    width = vol_normalized[level]
    fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", 
                             line=dict(width=width), name=f'Support {level} Vol: {vol_profile[level]}'))

# for level in resistance_levels:
#     width = vol_normalized[level]
#     fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", 
#                              line=dict(width=width), name=f'Resistance {level} Vol: {vol_profile[level]}'))

fig.update_layout(title='BTC-USD', xaxis_rangeslider_visible=False)
fig.show()


In [ ]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

data = btcusd_data

# Create a slider to select the number of days to go back
days_to_include = 10000 # st.slider('Number of days to consider:', 1, len(data), len(data))

# Filter the data based on the days selected
data = data.iloc[-days_to_include:]

num_bars = 10
bin_percentage = 10

data['Bin_Width'] = data['Last'] * bin_percentage / 100
bins = [data['Last'].iloc[0] - data['Bin_Width'].iloc[0]]
for i in range(1, len(data)):
    bins.append(bins[-1] + (data['Bin_Width'].iloc[i] + data['Bin_Width'].iloc[i-1]) / 2)

data['Bin'] = pd.cut(data['Last'], bins, labels=(bins[:-1]), include_lowest=True)
binned_volume = data.groupby('Bin').size()
top_bins = binned_volume.nlargest(num_bars)

vol_normalized = (top_bins - top_bins.min()) / (top_bins.max() - top_bins.min()) * 4 + 1

fig = go.Figure(data=[go.Candlestick(x=data.index,
                open=data['First'],
                high=data['High'],
                low=data['Low'],
                close=data['Last'])])

for level, vol in top_bins.items():
    width = vol_normalized[level]
    fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", 
                                line=dict(width=width), name=f'Level {level} Vol: {vol}'))

fig.update_layout(title='BTC-USD', xaxis_rangeslider_visible=False)
fig.show()


In [ ]:
todo zeit mit rein so wie resistence seit 2 jahren ...

SyntaxError: invalid syntax (774269896.py, line 1)